# Trexquant Interview Project (The Hangman Game)

* Copyright Trexquant Investment LP. All Rights Reserved.
* Redistribution of this question without written consent from Trexquant is prohibited

## Instruction:
For this coding test, your mission is to write an algorithm that plays the game of Hangman through our API server.

When a user plays Hangman, the server first selects a secret word at random from a list. The server then returns a row of underscores (space separated)—one for each letter in the secret word—and asks the user to guess a letter. If the user guesses a letter that is in the word, the word is redisplayed with all instances of that letter shown in the correct positions, along with any letters correctly guessed on previous turns. If the letter does not appear in the word, the user is charged with an incorrect guess. The user keeps guessing letters until either (1) the user has correctly guessed all the letters in the word
or (2) the user has made six incorrect guesses.

You are required to write a "guess" function that takes current word (with underscores) as input and returns a guess letter. You will use the API codes below to play 1,000 Hangman games. You have the opportunity to practice before you want to start recording your game results.

Your algorithm is permitted to use a training set of approximately 250,000 dictionary words. Your algorithm will be tested on an entirely disjoint set of 250,000 dictionary words. Please note that this means the words that you will ultimately be tested on do NOT appear in the dictionary that you are given. You are not permitted to use any dictionary other than the training dictionary we provided. This requirement will be strictly enforced by code review.

You are provided with a basic, working algorithm. This algorithm will match the provided masked string (e.g. a _ _ l e) to all possible words in the dictionary, tabulate the frequency of letters appearing in these possible words, and then guess the letter with the highest frequency of appearence that has not already been guessed. If there are no remaining words that match then it will default back to the character frequency distribution of the entire dictionary.

This benchmark strategy is successful approximately 18% of the time. Your task is to design an algorithm that significantly outperforms this benchmark.

In [1]:
import json
import requests
import random
import string
import secrets
import time
import re
import collections
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, LSTM, Dense, Embedding, Dropout, Add, Attention, Concatenate
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.callbacks import ModelCheckpoint
from sklearn.model_selection import train_test_split
from collections import deque

try:
    from urllib.parse import parse_qs, urlencode, urlparse
except ImportError:
    from urlparse import parse_qs, urlparse
    from urllib import urlencode

from requests.packages.urllib3.exceptions import InsecureRequestWarning

requests.packages.urllib3.disable_warnings(InsecureRequestWarning)

2024-08-16 02:57:34.359721: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-08-16 02:57:34.359831: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-08-16 02:57:34.490802: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [2]:
# External code for training the LSTM model

def load_dictionary(file_path):
    with open(file_path, 'r') as file:
        words = file.read().splitlines()
    return words

# Load the training dictionary
words = load_dictionary('/kaggle/input/train-data/words_250000_train.txt')

# Define vocabulary
vocab = list(string.ascii_lowercase) + ['_']  # Adjust this as per your requirements
vocab_size = len(vocab)
char_to_idx = {char: i for i, char in enumerate(vocab)}
idx_to_char = {i: char for i, char in enumerate(vocab)}

# Analyze word length distribution
word_lengths = [len(word) for word in words]
average_length = sum(word_lengths) / len(word_lengths)
median_length = sorted(word_lengths)[len(word_lengths) // 2]
max_length = max(word_lengths)

print("Average word length:", average_length)
print("Median word length:", median_length)

Average word length: 9.347760668719754
Median word length: 9


In [3]:
# One-hot encoding utility
def one_hot_encode(sequence):
    one_hot = [[0] * vocab_size for _ in range(len(sequence))]
    for i, index in enumerate(sequence):
        if index != -1:  # Ensure we don't encode -1 (padding value)
            one_hot[i][index] = 1
    return np.array(one_hot)

# Model Building
def build_hangman_model(input_length, vocab_size):
    # Encoder
    encoder_inputs = Input(shape=(input_length, vocab_size))
    encoder_lstm = LSTM(128, return_sequences=True, return_state=True)
    encoder_outputs, forward_h, forward_c = encoder_lstm(encoder_inputs)

    # Decoder
    decoder_inputs = Input(shape=(input_length, vocab_size))
    decoder_lstm = LSTM(128, return_sequences=True, return_state=True)
    decoder_outputs, _, _ = decoder_lstm(decoder_inputs, initial_state=[forward_h, forward_c])
    
    # Dense output layer applied to decoder outputs
    decoder_dense = Dense(vocab_size, activation='softmax')
    decoder_outputs = decoder_dense(decoder_outputs)
    
    model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
    model.compile(optimizer=tf.keras.optimizers.Adam(), loss='categorical_crossentropy', metrics=['accuracy'])
    return model

# DQN Agent Class
class DQNAgent:
    def __init__(self, model, vocab_size, state_size, max_tries):
        self.model = model
        self.memory = deque(maxlen=2000)
        self.gamma = 0.95
        self.epsilon = 1.0
        self.epsilon_min = 0.01
        self.epsilon_decay = 0.995
        self.learning_rate = 0.001
        self.state_size = state_size
        self.action_size = vocab_size
        self.max_tries = max_tries
        self.model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=self.learning_rate), loss='categorical_crossentropy')

    def act(self, state, guessed_chars):
        pos = np.random.choice(range(self.state_size))
        
        if np.random.rand() <= self.epsilon:
            return char_to_idx[np.random.choice(list(set(vocab) - guessed_chars))], pos  # Explore
        
        q_values = self.model.predict([state.reshape(1, -1, vocab_size), np.zeros((1, max_length, vocab_size))])
        action = 0
        max_q = 0
        for i in range(len(q_values[0])):
            while max_q < np.amax(q_values[0][i]):
                if idx_to_char[np.argmax(q_values[0][i])] in guessed_chars:
                    q_values[0][i][np.argmax(q_values[0][i])] = 0
                    continue
                max_q = np.amax(q_values[0][i])
                pos = i
                action = np.argmax(q_values[0][i])
                
        while idx_to_char[action] in guessed_chars:  # Ensure no repeated guesses
            action = char_to_idx[np.random.choice(list(set(vocab) - guessed_chars))]
            
        return action, pos  # Exploit

    def remember(self, state, action, pos, reward, next_state, done):
        self.memory.append((state, action, pos, reward, next_state, done))

    def replay(self, batch_size=32):
        if len(self.memory) < batch_size:
            return
        minibatch = random.sample(self.memory, batch_size)
        for state, action, pos, reward, next_state, done in minibatch:
            target = reward
            q_values = self.model.predict([next_state.reshape(1, -1, vocab_size), np.zeros((1, max_length, vocab_size))])           
            if not done:
                max_q = 0
                for i in range(len(q_values[0])):
                    if max_q < np.amax(q_values[0][i]):
                        max_q = np.amax(q_values[0][i])
                target += self.gamma * max_q
            target_f = np.zeros_like(q_values)
            target_f[0] = q_values[0]  # Copy existing Q-values
            target_f[0][pos][action] = target
            self.model.fit([state.reshape(1, -1, vocab_size), np.zeros((1, max_length, vocab_size))], target_f, epochs=1, verbose=1)
        if self.epsilon > self.epsilon_min:
            self.epsilon *= self.epsilon_decay


def prepare_state(state):
    integer_encoded = np.array([char_to_idx[char] for char in state])
    padded_state = pad_sequences([integer_encoded], maxlen=max_length, padding='post', truncating='post', value=-1)
    return padded_state[0]

# Simulate Hangman Game
def simulate_hangman_game(agent, word, vocab, max_length):
    state = "_" * len(word)
    guessed_chars = set()
    incorrect_guesses = 0
    max_tries = agent.max_tries

    while incorrect_guesses < max_tries and "_" in state:
        state_encoded = prepare_state(state)
        action, pos = agent.act(one_hot_encode(state_encoded), guessed_chars)
        guessed_char = idx_to_char[action]
        next_state = state

        if guessed_char in word and guessed_char not in guessed_chars:
            guessed_chars.add(guessed_char)
            next_state = "".join([char if char in guessed_chars else "_" for char in word])
            reward = 1 + 0.5 * (len(guessed_chars) - state.count('_'))
        else:
            guessed_chars.add(guessed_char)
            incorrect_guesses += 1
            reward = -1 - 0.5 * incorrect_guesses

        done = incorrect_guesses >= max_tries or "_" not in state
        agent.remember(one_hot_encode(state_encoded), action, pos, reward, one_hot_encode(prepare_state(next_state)), done)
        state = next_state

        if done:
            break

model_checkpoint_path = '/kaggle/working/rl_based_hangman_model.keras'
model_checkpoint_callback = ModelCheckpoint(
    filepath=model_checkpoint_path,
    save_best_only=True,
    monitor='loss',
    mode='min'
)

# Training the DQN Agent
def train_dqn(agent, words, vocab, episodes=1000, batch_size=32):
    for episode in range(episodes):
        word = random.choice(words)
        simulate_hangman_game(agent, word, vocab, max_length)
        agent.replay(batch_size)
        
        # Log progress every episode
        if episode % 100 == 0:
            print(f"Episode {episode}/{episodes} completed")

    # Save the final model
    agent.model.save(model_checkpoint_path)
    print(f"Model saved to {model_checkpoint_path}")

# Initialize and train the DQN Agent
model = build_hangman_model(input_length=max_length, vocab_size=vocab_size)
agent = DQNAgent(model, vocab_size=vocab_size, state_size=max_length, max_tries=6)

train_dqn(agent, words, vocab)

Episode 0/1000 completed
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 403ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 3s 3s/step - loss: 3.0115
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step - loss: 3.3525
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - loss: 2.8983
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step - loss: 3.1252
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - loss: 2.8975
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - loss: 2.8411
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step - loss: 3.1252
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step - loss: 2.8365
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - loss: 3.0097
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - loss: 3.2387
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 